<a href="https://colab.research.google.com/github/Mburu-Elvis/Nairobi_Metropolitan_House_Price_Prediction/blob/main/mansiondeal.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [81]:
! pip install ydata_profiling
! pip install category_encoders

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.9/81.9 kB 2.1 MB/s eta 0:00:00


In [82]:
import pandas as pd
import numpy as np
from ydata_profiling import ProfileReport
import seaborn as sns
import matplotlib.pyplot as plt

from category_encoders import TargetEncoder

In [83]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [84]:
house_data = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/Data/mansiondeal.csv')

## Exploratory Data Analysis

In [85]:
profile = ProfileReport(house_data, title="Nairobi House Rent Prices", explorative=True)

profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### Data Preprocessing

In [86]:
house_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1099 entries, 0 to 1098
Data columns (total 11 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   Location      1099 non-null   object 
 1   Description   1099 non-null   object 
 2   Bedrooms      1099 non-null   object 
 3   Bathrooms     1091 non-null   float64
 4   Living Rooms  1099 non-null   int64  
 5   Kitchen       1099 non-null   object 
 6   Price         1099 non-null   object 
 7   Water         1099 non-null   object 
 8   Electricity   1099 non-null   object 
 9   Garden        1099 non-null   object 
 10  Pool          1099 non-null   object 
dtypes: float64(1), int64(1), object(9)
memory usage: 94.6+ KB


In [87]:
house_data['Location'] = house_data['Location'].str.split(',').str[0]

print(house_data['Location'].head())

0            Karen
1    Spring Valley
2        Riverside
3        Riverside
4         Kitisuru
Name: Location, dtype: object


In [88]:
house_data['Location'].value_counts()

Lavington          132
Karen              131
Westlands           87
Runda               76
Langata             67
                  ... 
David Osieli Rd      1
Ndoto Road           1
Kanjata Road         1
Ruiru                1
Karen Plains         1
Name: Location, Length: 171, dtype: int64

In [89]:
# Bedrooms
house_data['Bedrooms'].info()

<class 'pandas.core.series.Series'>
RangeIndex: 1099 entries, 0 to 1098
Series name: Bedrooms
Non-Null Count  Dtype 
--------------  ----- 
1099 non-null   object
dtypes: object(1)
memory usage: 8.7+ KB


In [90]:
house_data['Bedrooms'].value_counts()

4            359
3            253
5            229
2            127
1             51
6             35
0             29
7              8
8              4
bedsitter      3
4+3            1
Name: Bedrooms, dtype: int64

In [91]:
house_data['Bedrooms'] = house_data['Bedrooms'].replace('bedsitter', '0')

In [92]:
house_data['Bedrooms'].value_counts()

4      359
3      253
5      229
2      127
1       51
6       35
0       32
7        8
8        4
4+3      1
Name: Bedrooms, dtype: int64

In [93]:
house_data.loc[house_data['Bedrooms'] == '4+3']

Location                                        Description Bedrooms  \
18    Runda  Stunning four bedroom + a gym which was conver...      4+3   

    Bathrooms  Living Rooms Kitchen        Price Water Electricity  \
18        5.0             1       ?  ksh 300,000     ✅           ✅   

         Garden              Pool  
18  ✅ A Garden   NO Swimming Pool

In [94]:
house_data['Bedrooms'] = house_data['Bedrooms'].replace('4+3', '4')

In [95]:
house_data['Bedrooms'].value_counts()

4    360
3    253
5    229
2    127
1     51
6     35
0     32
7      8
8      4
Name: Bedrooms, dtype: int64

In [96]:
house_data['Bedrooms'] = pd.to_numeric(house_data['Bedrooms'])

In [97]:
# Bathrooms

house_data['Bathrooms'].info()

<class 'pandas.core.series.Series'>
RangeIndex: 1099 entries, 0 to 1098
Series name: Bathrooms
Non-Null Count  Dtype  
--------------  -----  
1091 non-null   float64
dtypes: float64(1)
memory usage: 8.7 KB


In [98]:
house_data['Bathrooms'].value_counts()

4.0    285
2.0    210
5.0    205
3.0    205
1.0     89
6.0     81
7.0      8
8.0      4
0.0      4
Name: Bathrooms, dtype: int64

In [99]:
# Price

house_data['Price'].info()

<class 'pandas.core.series.Series'>
RangeIndex: 1099 entries, 0 to 1098
Series name: Price
Non-Null Count  Dtype 
--------------  ----- 
1099 non-null   object
dtypes: object(1)
memory usage: 8.7+ KB


In [100]:
house_data['Price'] = house_data['Price'].str.replace('ksh ', '')
house_data['Price'] = house_data['Price'].str.replace(',', '')

In [101]:
house_data['Price'] = pd.to_numeric(house_data['Price'])
print(house_data['Price'].head())

0    400000
1    260000
2    180000
3    500000
4    750000
Name: Price, dtype: int64


In [102]:
house_data['Garden'].info()

<class 'pandas.core.series.Series'>
RangeIndex: 1099 entries, 0 to 1098
Series name: Garden
Non-Null Count  Dtype 
--------------  ----- 
1099 non-null   object
dtypes: object(1)
memory usage: 8.7+ KB


In [103]:
house_data.loc[house_data['Pool'] == '✅ Heated Swimming Pool']

Location                                        Description  Bedrooms  \
661    Runda  Located in a gated community and at a price of...         5   

     Bathrooms  Living Rooms Kitchen   Price Water Electricity       Garden  \
661        6.0             1       ?  530000     ✅           ✅  ✅ A Garden    

                       Pool  
661  ✅ Heated Swimming Pool

In [104]:
house_data['Pool'] = house_data['Pool'].str.replace('✅ Heated Swimming Pool', '✅ Swimming Pool')

In [105]:
house_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1099 entries, 0 to 1098
Data columns (total 11 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   Location      1099 non-null   object 
 1   Description   1099 non-null   object 
 2   Bedrooms      1099 non-null   int64  
 3   Bathrooms     1091 non-null   float64
 4   Living Rooms  1099 non-null   int64  
 5   Kitchen       1099 non-null   object 
 6   Price         1099 non-null   int64  
 7   Water         1099 non-null   object 
 8   Electricity   1099 non-null   object 
 9   Garden        1099 non-null   object 
 10  Pool          1099 non-null   object 
dtypes: float64(1), int64(3), object(7)
memory usage: 94.6+ KB


### Data Cleaning

In [106]:
house_data['Bathrooms'].describe()

count    1091.000000
mean        3.540788
std         1.466737
min         0.000000
25%         2.000000
50%         4.000000
75%         5.000000
max         8.000000
Name: Bathrooms, dtype: float64

In [107]:
house_data['Bathrooms'].fillna(house_data['Bathrooms'].mean(), inplace=True)

In [108]:
house_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1099 entries, 0 to 1098
Data columns (total 11 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   Location      1099 non-null   object 
 1   Description   1099 non-null   object 
 2   Bedrooms      1099 non-null   int64  
 3   Bathrooms     1099 non-null   float64
 4   Living Rooms  1099 non-null   int64  
 5   Kitchen       1099 non-null   object 
 6   Price         1099 non-null   int64  
 7   Water         1099 non-null   object 
 8   Electricity   1099 non-null   object 
 9   Garden        1099 non-null   object 
 10  Pool          1099 non-null   object 
dtypes: float64(1), int64(3), object(7)
memory usage: 94.6+ KB


In [109]:
profile = ProfileReport(house_data, title="Nairobi House Rent Prices", explorative=True)

profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [110]:
house_data.drop_duplicates(keep='first', inplace=True)

In [111]:
house_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1067 entries, 0 to 1098
Data columns (total 11 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   Location      1067 non-null   object 
 1   Description   1067 non-null   object 
 2   Bedrooms      1067 non-null   int64  
 3   Bathrooms     1067 non-null   float64
 4   Living Rooms  1067 non-null   int64  
 5   Kitchen       1067 non-null   object 
 6   Price         1067 non-null   int64  
 7   Water         1067 non-null   object 
 8   Electricity   1067 non-null   object 
 9   Garden        1067 non-null   object 
 10  Pool          1067 non-null   object 
dtypes: float64(1), int64(3), object(7)
memory usage: 100.0+ KB


### Data preparation for modelling

***Dropping Features that will not be relevant in training the ML model***

In [112]:
columns = ['Description', 'Living Rooms', 'Kitchen', 'Water', 'Electricity']

house_data = house_data.drop(columns, axis=1)

In [113]:
house_data.head()

Location  Bedrooms  Bathrooms   Price       Garden              Pool
0          Karen         5        5.0  400000  ✅ A Garden   NO Swimming Pool
1  Spring Valley         5        5.0  260000  ✅ A Garden   NO Swimming Pool
2      Riverside         3        3.0  180000  ✅ A Garden    ✅ Swimming Pool
3      Riverside         5        5.0  500000  ✅ A Garden   NO Swimming Pool
4       Kitisuru         4        5.0  750000  ✅ A Garden    ✅ Swimming Pool

In [114]:
from sklearn.model_selection import train_test_split

In [115]:
X_Train, X_test, y_train, y_test = train_test_split(house_data.drop(columns=['Price']),house_data['Price'], test_size=0.2, random_state=42)

In [116]:
encoder = TargetEncoder(cols=['Location'])

In [117]:
X_Train_encoded = encoder.fit_transform(X_Train, y_train)
X_test_encoded = encoder.transform(X_test)

In [118]:
one_hot_encoded_data_train = pd.get_dummies(X_Train_encoded, columns=['Garden', 'Pool'])
one_hot_endoded_data_test = pd.get_dummies(X_test_encoded, columns=['Garden', 'Pool'])

In [119]:
one_hot_encoded_data_train.head()

Location  Bedrooms  Bathrooms  Garden_NO Garden  Garden_✅ A Garden   \
346  163870.073547         2        2.0                 0                   1   
107  233293.444877         5        6.0                 0                   1   
602  218244.065727         3        2.0                 0                   1   
55   205548.395418         3        2.0                 0                   1   
225  224761.747581         2        2.0                 0                   1   

     Pool_NO Swimming Pool  Pool_✅ Swimming Pool  
346                      0                     1  
107                      1                     0  
602                      0                     1  
55                       0                     1  
225                      0                     1

## Modelling

In [126]:
from  sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error
from sklearn.metrics import r2_score

In [127]:
model = LinearRegression()

In [128]:
model.fit(one_hot_encoded_data_train, y_train)

LinearRegression()

In [129]:
predictions = model.predict(one_hot_endoded_data_test)

In [130]:
mse = mean_squared_error(y_test, predictions)

In [131]:
mse

11435370113.169607

In [132]:
score = r2_score(y_test, predictions)

In [133]:
score

0.3882377649515978